In [45]:
# data analysis and wrangling
import pandas as pd
import numpy as np
import random as rnd

# visualization
import seaborn as sns
import matplotlib.pyplot as plt
%matplotlib inline

# machine learning
from sklearn.linear_model import LogisticRegression
from sklearn.ensemble import RandomForestClassifier
from sklearn.tree import DecisionTreeClassifier
from sklearn.model_selection import GridSearchCV
from sklearn.linear_model import Perceptron
from sklearn.model_selection import KFold

import pdb

# 1. 데이터셋 연결, 결측값 확인

In [46]:
train_df = pd.read_csv('./train.csv')
test_df = pd.read_csv('./test.csv')
combine = [train_df, test_df] # 데이터 프레임 두개를 한번에 저장한 리스트 타입의 변수 선언

# preview the data
train_df.info()
print('_'*40)
test_df.info()
print('_'*40)
print(combine)

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 891 entries, 0 to 890
Data columns (total 12 columns):
 #   Column       Non-Null Count  Dtype  
---  ------       --------------  -----  
 0   PassengerId  891 non-null    int64  
 1   Survived     891 non-null    int64  
 2   Pclass       891 non-null    int64  
 3   Name         891 non-null    object 
 4   Sex          891 non-null    object 
 5   Age          714 non-null    float64
 6   SibSp        891 non-null    int64  
 7   Parch        891 non-null    int64  
 8   Ticket       891 non-null    object 
 9   Fare         891 non-null    float64
 10  Cabin        204 non-null    object 
 11  Embarked     889 non-null    object 
dtypes: float64(2), int64(5), object(5)
memory usage: 83.7+ KB
________________________________________
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 418 entries, 0 to 417
Data columns (total 11 columns):
 #   Column       Non-Null Count  Dtype  
---  ------       --------------  -----  
 0   Passenger

In [47]:
train_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 891 entries, 0 to 890
Data columns (total 12 columns):
 #   Column       Non-Null Count  Dtype  
---  ------       --------------  -----  
 0   PassengerId  891 non-null    int64  
 1   Survived     891 non-null    int64  
 2   Pclass       891 non-null    int64  
 3   Name         891 non-null    object 
 4   Sex          891 non-null    object 
 5   Age          714 non-null    float64
 6   SibSp        891 non-null    int64  
 7   Parch        891 non-null    int64  
 8   Ticket       891 non-null    object 
 9   Fare         891 non-null    float64
 10  Cabin        204 non-null    object 
 11  Embarked     889 non-null    object 
dtypes: float64(2), int64(5), object(5)
memory usage: 83.7+ KB


In [48]:
# train의 데이터셋은 11개, 테스트 데이터셋은 10개임 -> test 데이터셋에는 survived 피처가 없음
print("After", train_df.shape, test_df.shape, combine[0].shape, combine[1].shape)

After (891, 12) (418, 11) (891, 12) (418, 11)


# 해당 인물에 특정한 문자열을 추출
- 정규식을 활용하여 이름에서 성별, 나이, 선실의 등급을 특정할 수 있는 문자열을 추출
- 이때, 정규식은 Name 피처에서 "," 와  "." 사이의 문자열을 추출한다
- 존칭을 통하여 해당 인물의 성별, 나이, 계급, 재력 등 생존과 연관성 있는 정보를 얻을 수 있음 


In [49]:
# Extract string  from 'Name'
# combine : A list variable combined to train and test dataset
    
for dataset in combine:
    dataset['Title'] = dataset.Name.str.extract(' ([A-Za-z]+)\.', expand=False)

In [50]:
train_df['Title'].unique()

array(['Mr', 'Mrs', 'Miss', 'Master', 'Don', 'Rev', 'Dr', 'Mme', 'Ms',
       'Major', 'Lady', 'Sir', 'Mlle', 'Col', 'Capt', 'Countess',
       'Jonkheer'], dtype=object)

In [51]:
# Based on a specific string extracted from the name, confirm the survival rate according to gender and marital status.

for dataset in combine:
    dataset['Title'] = dataset['Title'].replace(['Dr','Rev'],'Rare')
    dataset['Title'] = dataset['Title'].replace(['Mlle','Lady','Ms','Countess'], 'Miss')
    dataset['Title'] = dataset['Title'].replace(['Mme','Dona'], 'Mrs')
    dataset['Title'] = dataset['Title'].replace(['Capt','Col','Don','Major','Sir','Jonkheer'], 'Master')
    
train_df[['Title', 'Survived']].groupby(['Title'], as_index=False).mean()

Title  Survived
0  Master  0.541667
1    Miss  0.705882
2      Mr  0.156673
3     Mrs  0.793651
4    Rare  0.230769

In [52]:
# title 별로 성비를 확인한다
# 시대상적으로 깊게 잠재되어 있는 "Lady First" 문화로 인해  
pd.crosstab(train_df['Title'], train_df['Sex'])

Sex     female  male
Title               
Master       0    48
Miss       187     0
Mr           0   517
Mrs        126     0
Rare         1    12

In [53]:
# Label encoding : title
title_mapping = {"Mr": 1, "Miss": 2, "Mrs": 3, "Master": 4, "Rare": 5}
for dataset in combine:
    dataset['Title'] = dataset['Title'].map(title_mapping)
    #dataset['Title'] = dataset['Title'].fillna(0)

# Label encoding : Sex
for dataset in combine:
    dataset['Sex'] = dataset['Sex'].map( {'female': 1, 'male': 0} ).astype(int)

# 이름에서 성별,혼인 여부 추출 완료
이름에서 추출된 문자열을 이용하여 "Title" 피처를 생성함.
고로 이름은 더 이상 의미 없는 피처로 간주, 티켓과 함께 추후 drop 진행

In [54]:
# 새로운 combine 실행
combine = [train_df, test_df]
train_df.shape, test_df.shape

((891, 13), (418, 12))

## Handling missing values in the "Age" feature
Create a 2-dimensional array with cabin class as rows and passenger gender as columns.
Calculate the mean age of passengers corresponding to each cell in the array.
Fill in missing values by inserting the average age corresponding to cabin class and gender for passengers with missing values.

In [55]:
# Create a 2-dimensional array with cabin class as rows and gender as columns.
guess_ages = np.zeros((2,3))
guess_ages

for dataset in combine:
    for i in range(0, 2):
        #pdb.set_trace()
        for j in range(0, 3):
            guess_df = dataset[(dataset['Sex'] == i) & (dataset['Pclass'] == j+1)]['Age'].dropna()
            # dataset['Sex'] == i) & (dataset['Pclass'] == j+1) == true 인 애트리뷰트 중 결측값이 있으면 결측값 삭제
            print("guess_df:")
            print(guess_df)
            print('*'*40)
            print(guess_ages)
            print('*'*40)            
           
            age_guess = guess_df.median()
            # Convert random age float to nearest .5 age
            guess_ages[i,j] = int(age_guess/0.5 + 0.5 ) * 0.5
            print(int(age_guess/0.5 + 0.5 ) * 0.5)
            #guess_ages_pd = pd.DataFrame(guess_ages)

guess_df:
6      54.0
23     28.0
27     19.0
30     40.0
34     28.0
       ... 
822    38.0
857    51.0
867    31.0
872    33.0
889    26.0
Name: Age, Length: 101, dtype: float64
****************************************
[[0. 0. 0.]
 [0. 0. 0.]]
****************************************
40.0
guess_df:
20     35.0
21     34.0
33     66.0
70     32.0
72     21.0
       ... 
848    28.0
861    21.0
864    24.0
883    28.0
886    27.0
Name: Age, Length: 99, dtype: float64
****************************************
[[40.  0.  0.]
 [ 0.  0.  0.]]
****************************************
30.0
guess_df:
0      22.0
4      35.0
7       2.0
12     20.0
13     39.0
       ... 
876    20.0
877    19.0
881    33.0
884    25.0
890    32.0
Name: Age, Length: 253, dtype: float64
****************************************
[[40. 30.  0.]
 [ 0.  0.  0.]]
****************************************
25.0
guess_df:
1      38.0
3      35.0
11     58.0
52     49.0
61     38.0
       ... 
856    45.0
862    48.0
871 

In [56]:
for dataset in combine:
    for i in range(0, 2):
        for j in range(0, 3):
            dataset.loc[ (dataset.Age.isnull()) & (dataset.Sex == i) & (dataset.Pclass == j+1),'Age'] = guess_ages[i,j]

    dataset['Age'] = dataset['Age'].astype(int)

In [57]:
train_df.head()

PassengerId  Survived  Pclass  \
0            1         0       3   
1            2         1       1   
2            3         1       3   
3            4         1       1   
4            5         0       3   

                                                Name  Sex  Age  SibSp  Parch  \
0                            Braund, Mr. Owen Harris    0   22      1      0   
1  Cumings, Mrs. John Bradley (Florence Briggs Th...    1   38      1      0   
2                             Heikkinen, Miss. Laina    1   26      0      0   
3       Futrelle, Mrs. Jacques Heath (Lily May Peel)    1   35      1      0   
4                           Allen, Mr. William Henry    0   35      0      0   

             Ticket     Fare Cabin Embarked  Title  
0         A/5 21171   7.2500   NaN        S      1  
1          PC 17599  71.2833   C85        C      3  
2  STON/O2. 3101282   7.9250   NaN        S      2  
3            113803  53.1000  C123        S      3  
4            373450   8.0500   NaN        S      1

## Convert the "Age" feature into categorical
Transform the continuous age feature into simple numerical data by dividing it into specific ranges.

In [58]:
# Divide the entire range of train_df into 5 intervals.
train_df['AgeBand'] = pd.cut(train_df['Age'], 5)

# Analyze the average survival rates of the 5 divided intervals.
train_df[['AgeBand', 'Survived']].groupby(['AgeBand'], as_index=False).mean().sort_values(by='AgeBand', ascending=True)

AgeBand  Survived
0  (-0.08, 16.0]  0.550000
1   (16.0, 32.0]  0.337374
2   (32.0, 48.0]  0.412037
3   (48.0, 64.0]  0.434783
4   (64.0, 80.0]  0.090909

In [59]:
# Perform label encoding on the 5 divided intervals.
for dataset in combine:    
    dataset.loc[ dataset['Age'] <= 16, 'Age'] = 0
    dataset.loc[(dataset['Age'] > 16) & (dataset['Age'] <= 32), 'Age'] = 1
    dataset.loc[(dataset['Age'] > 32) & (dataset['Age'] <= 48), 'Age'] = 2
    dataset.loc[(dataset['Age'] > 48) & (dataset['Age'] <= 64), 'Age'] = 3
    dataset.loc[ dataset['Age'] > 64, 'Age']

train_df = train_df.drop(['AgeBand'], axis=1)
combine = [train_df, test_df]
train_df.head()

PassengerId  Survived  Pclass  \
0            1         0       3   
1            2         1       1   
2            3         1       3   
3            4         1       1   
4            5         0       3   

                                                Name  Sex  Age  SibSp  Parch  \
0                            Braund, Mr. Owen Harris    0    1      1      0   
1  Cumings, Mrs. John Bradley (Florence Briggs Th...    1    2      1      0   
2                             Heikkinen, Miss. Laina    1    1      0      0   
3       Futrelle, Mrs. Jacques Heath (Lily May Peel)    1    2      1      0   
4                           Allen, Mr. William Henry    0    2      0      0   

             Ticket     Fare Cabin Embarked  Title  
0         A/5 21171   7.2500   NaN        S      1  
1          PC 17599  71.2833   C85        C      3  
2  STON/O2. 3101282   7.9250   NaN        S      2  
3            113803  53.1000  C123        S      3  
4            373450   8.0500   NaN        S      1

## Consider the number of accompanying parents/children and the number of accompanying siblings/spouses as a single feature. 
Create a new feature called "FamilySize" as the sum of "SibSp" + "Parch" + 1, intending to drop "SibSp" and "Parch".

In [60]:
for dataset in combine:
    dataset['FamilySize'] = dataset['SibSp'] + dataset['Parch'] + 1 # Total number of individuals in one family
    
# Group the survival rates based on Family Size, print the mean values, and output them in descending order of survival rates.
train_df[['FamilySize', 'Survived']].groupby(['FamilySize'], as_index=False).mean().sort_values(by='Survived', ascending=False)

FamilySize  Survived
3           4  0.724138
2           3  0.578431
1           2  0.552795
6           7  0.333333
0           1  0.303538
4           5  0.200000
5           6  0.136364
7           8  0.000000
8          11  0.000000

In [61]:
test_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 418 entries, 0 to 417
Data columns (total 13 columns):
 #   Column       Non-Null Count  Dtype  
---  ------       --------------  -----  
 0   PassengerId  418 non-null    int64  
 1   Pclass       418 non-null    int64  
 2   Name         418 non-null    object 
 3   Sex          418 non-null    int64  
 4   Age          418 non-null    int64  
 5   SibSp        418 non-null    int64  
 6   Parch        418 non-null    int64  
 7   Ticket       418 non-null    object 
 8   Fare         417 non-null    float64
 9   Cabin        91 non-null     object 
 10  Embarked     418 non-null    object 
 11  Title        418 non-null    int64  
 12  FamilySize   418 non-null    int64  
dtypes: float64(1), int64(8), object(4)
memory usage: 42.6+ KB


In [62]:
# Processing for solo passengers
for dataset in combine:
    dataset['IsAlone'] = 0
    dataset.loc[dataset['FamilySize'] == 1, 'IsAlone'] = 1

pd.crosstab(train_df['IsAlone'], train_df['Sex'])
# Sex { 0 : male, 1 : female}

Sex        0    1
IsAlone          
0        166  188
1        411  126

for dataset in combine:
    dataset['Age*Class'] = dataset.Age * dataset.Pclass

train_df.loc[:, ['Age*Class', 'Age', 'Pclass']].head(10)

#train_df[['IsAlone', 'Sex']].groupby(['Sex'], as_index=False).mean()

# embarked 데이터의 결측치 2건
결측값은 단 2건, 최빈값 S로 해결

In [63]:
freq_port = train_df.Embarked.dropna().mode()[0]
# mode() : 최빈값

for dataset in combine:
    dataset['Embarked'] = dataset['Embarked'].fillna(freq_port)
    
train_df[['Embarked', 'Survived']].groupby(['Embarked'], as_index=False).mean().sort_values(by='Survived', ascending=False)

Embarked  Survived
0        C  0.553571
1        Q  0.389610
2        S  0.339009

In [64]:
test_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 418 entries, 0 to 417
Data columns (total 14 columns):
 #   Column       Non-Null Count  Dtype  
---  ------       --------------  -----  
 0   PassengerId  418 non-null    int64  
 1   Pclass       418 non-null    int64  
 2   Name         418 non-null    object 
 3   Sex          418 non-null    int64  
 4   Age          418 non-null    int64  
 5   SibSp        418 non-null    int64  
 6   Parch        418 non-null    int64  
 7   Ticket       418 non-null    object 
 8   Fare         417 non-null    float64
 9   Cabin        91 non-null     object 
 10  Embarked     418 non-null    object 
 11  Title        418 non-null    int64  
 12  FamilySize   418 non-null    int64  
 13  IsAlone      418 non-null    int64  
dtypes: float64(1), int64(9), object(4)
memory usage: 45.8+ KB


In [65]:
# 결측치 replace 후 원핫 인코딩
for dataset in combine:
    dataset['Embarked'] = dataset['Embarked'].map( {'S': 0, 'C': 1, 'Q': 2} ).astype(int)

train_df.head()

PassengerId  Survived  Pclass  \
0            1         0       3   
1            2         1       1   
2            3         1       3   
3            4         1       1   
4            5         0       3   

                                                Name  Sex  Age  SibSp  Parch  \
0                            Braund, Mr. Owen Harris    0    1      1      0   
1  Cumings, Mrs. John Bradley (Florence Briggs Th...    1    2      1      0   
2                             Heikkinen, Miss. Laina    1    1      0      0   
3       Futrelle, Mrs. Jacques Heath (Lily May Peel)    1    2      1      0   
4                           Allen, Mr. William Henry    0    2      0      0   

             Ticket     Fare Cabin  Embarked  Title  FamilySize  IsAlone  
0         A/5 21171   7.2500   NaN         0      1           2        0  
1          PC 17599  71.2833   C85         1      3           2        0  
2  STON/O2. 3101282   7.9250   NaN         0      2           1        1  
3            113803  53.1000  C123         0      3           2        0  
4            373450   8.0500   NaN         0      1           1        1

# fare 피처의 결측값 처리
티켓의 가격은 선실의 등급으로 대체 가능한 데이터 -> drop 할수는 없으니, 결측값은 중앙값으로 처리

In [66]:
test_df['Fare'].fillna(test_df['Fare'].dropna().median(), inplace=True)
test_df.head()

PassengerId  Pclass                                          Name  Sex  \
0          892       3                              Kelly, Mr. James    0   
1          893       3              Wilkes, Mrs. James (Ellen Needs)    1   
2          894       2                     Myles, Mr. Thomas Francis    0   
3          895       3                              Wirz, Mr. Albert    0   
4          896       3  Hirvonen, Mrs. Alexander (Helga E Lindqvist)    1   

   Age  SibSp  Parch   Ticket     Fare Cabin  Embarked  Title  FamilySize  \
0    2      0      0   330911   7.8292   NaN         2      1           1   
1    2      1      0   363272   7.0000   NaN         0      3           2   
2    3      0      0   240276   9.6875   NaN         2      1           1   
3    1      0      0   315154   8.6625   NaN         0      1           1   
4    1      1      1  3101298  12.2875   NaN         0      3           3   

   IsAlone  
0        1  
1        0  
2        1  
3        1  
4        0

In [67]:
# Creating fare categories.
train_df['FareBand'] = pd.cut(train_df['Fare'], 4)
train_df[['FareBand', 'Survived']].groupby(['FareBand'], as_index=False).mean().sort_values(by='FareBand', ascending=True)

FareBand  Survived
0   (-0.512, 128.082]  0.368113
1  (128.082, 256.165]  0.724138
2  (256.165, 384.247]  0.666667
3  (384.247, 512.329]  1.000000

In [68]:
# Label encoding
for dataset in combine:
    dataset.loc[ dataset['Fare'] <= 7.91, 'Fare'] = 0
    dataset.loc[(dataset['Fare'] > 7.91) & (dataset['Fare'] <= 14.454), 'Fare'] = 1
    dataset.loc[(dataset['Fare'] > 14.454) & (dataset['Fare'] <= 31), 'Fare']   = 2
    dataset.loc[ dataset['Fare'] > 31, 'Fare'] = 3
    dataset['Fare'] = dataset['Fare'].astype(int)

train_df = train_df.drop(['FareBand'], axis=1)
combine = [train_df, test_df]
    
train_df.head(10)

PassengerId  Survived  Pclass  \
0            1         0       3   
1            2         1       1   
2            3         1       3   
3            4         1       1   
4            5         0       3   
5            6         0       3   
6            7         0       1   
7            8         0       3   
8            9         1       3   
9           10         1       2   

                                                Name  Sex  Age  SibSp  Parch  \
0                            Braund, Mr. Owen Harris    0    1      1      0   
1  Cumings, Mrs. John Bradley (Florence Briggs Th...    1    2      1      0   
2                             Heikkinen, Miss. Laina    1    1      0      0   
3       Futrelle, Mrs. Jacques Heath (Lily May Peel)    1    2      1      0   
4                           Allen, Mr. William Henry    0    2      0      0   
5                                   Moran, Mr. James    0    1      0      0   
6                            McCarthy, Mr. Timothy J    0    3      0      0   
7                     Palsson, Master. Gosta Leonard    0    0      3      1   
8  Johnson, Mrs. Oscar W (Elisabeth Vilhelmina Berg)    1    1      0      2   
9                Nasser, Mrs. Nicholas (Adele Achem)    1    0      1      0   

             Ticket  Fare Cabin  Embarked  Title  FamilySize  IsAlone  
0         A/5 21171     0   NaN         0      1           2        0  
1          PC 17599     3   C85         1      3           2        0  
2  STON/O2. 3101282     1   NaN         0      2           1        1  
3            113803     3  C123         0      3           2        0  
4            373450     1   NaN         0      1           1        1  
5            330877     1   NaN         2      1           1        1  
6             17463     3   E46         0      1           1        1  
7            349909     2   NaN         0      4           5        0  
8            347742     1   NaN         0      3           3        0  
9            237736     2   NaN         1      3           2        0

In [69]:
train_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 891 entries, 0 to 890
Data columns (total 15 columns):
 #   Column       Non-Null Count  Dtype 
---  ------       --------------  ----- 
 0   PassengerId  891 non-null    int64 
 1   Survived     891 non-null    int64 
 2   Pclass       891 non-null    int64 
 3   Name         891 non-null    object
 4   Sex          891 non-null    int64 
 5   Age          891 non-null    int64 
 6   SibSp        891 non-null    int64 
 7   Parch        891 non-null    int64 
 8   Ticket       891 non-null    object
 9   Fare         891 non-null    int64 
 10  Cabin        204 non-null    object
 11  Embarked     891 non-null    int64 
 12  Title        891 non-null    int64 
 13  FamilySize   891 non-null    int64 
 14  IsAlone      891 non-null    int64 
dtypes: int64(12), object(3)
memory usage: 104.5+ KB


In [70]:
train_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 891 entries, 0 to 890
Data columns (total 15 columns):
 #   Column       Non-Null Count  Dtype 
---  ------       --------------  ----- 
 0   PassengerId  891 non-null    int64 
 1   Survived     891 non-null    int64 
 2   Pclass       891 non-null    int64 
 3   Name         891 non-null    object
 4   Sex          891 non-null    int64 
 5   Age          891 non-null    int64 
 6   SibSp        891 non-null    int64 
 7   Parch        891 non-null    int64 
 8   Ticket       891 non-null    object
 9   Fare         891 non-null    int64 
 10  Cabin        204 non-null    object
 11  Embarked     891 non-null    int64 
 12  Title        891 non-null    int64 
 13  FamilySize   891 non-null    int64 
 14  IsAlone      891 non-null    int64 
dtypes: int64(12), object(3)
memory usage: 104.5+ KB


In [71]:
test_df.info()
# 결측값, 레이블 인코딩만 진행

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 418 entries, 0 to 417
Data columns (total 14 columns):
 #   Column       Non-Null Count  Dtype 
---  ------       --------------  ----- 
 0   PassengerId  418 non-null    int64 
 1   Pclass       418 non-null    int64 
 2   Name         418 non-null    object
 3   Sex          418 non-null    int64 
 4   Age          418 non-null    int64 
 5   SibSp        418 non-null    int64 
 6   Parch        418 non-null    int64 
 7   Ticket       418 non-null    object
 8   Fare         418 non-null    int64 
 9   Cabin        91 non-null     object
 10  Embarked     418 non-null    int64 
 11  Title        418 non-null    int64 
 12  FamilySize   418 non-null    int64 
 13  IsAlone      418 non-null    int64 
dtypes: int64(11), object(3)
memory usage: 45.8+ KB


# 모든 데이터의 범주화, Label Encoding 완료
이전 데이터보다 조금 더 간결해짐 -> 입력값으로 사용하기에 이전의 데이터보다 원활함

# 합치고 남은 데이터셋은 drop
합쳐져 원핫인코딩 되어 새로 만들어진 피처의 재료 피처들은 drop

In [72]:
# drop 만 모아놓음
train_df = train_df.drop(['Name','Ticket', 'Cabin','Parch', 'SibSp'], axis=1)
test_df = test_df.drop(['Name','Ticket', 'Cabin','Parch', 'SibSp'], axis=1)

combine = [train_df, test_df]

In [73]:
test_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 418 entries, 0 to 417
Data columns (total 9 columns):
 #   Column       Non-Null Count  Dtype
---  ------       --------------  -----
 0   PassengerId  418 non-null    int64
 1   Pclass       418 non-null    int64
 2   Sex          418 non-null    int64
 3   Age          418 non-null    int64
 4   Fare         418 non-null    int64
 5   Embarked     418 non-null    int64
 6   Title        418 non-null    int64
 7   FamilySize   418 non-null    int64
 8   IsAlone      418 non-null    int64
dtypes: int64(9)
memory usage: 29.5 KB


# 학습용, 테스트용 데이터 나누기

In [74]:
from sklearn.model_selection import train_test_split

# y_train 구성
y_train_df = train_df['Survived']
# x_train 을 위한  survived 값 드롭
X_train_df= train_df.drop('Survived',axis=1)

X_train, X_test, y_train, y_test=train_test_split(X_train_df, y_train_df, \
                                                  test_size=0.2, random_state=11)

In [75]:
train_df.head()

PassengerId  Survived  Pclass  Sex  Age  Fare  Embarked  Title  FamilySize  \
0            1         0       3    0    1     0         0      1           2   
1            2         1       1    1    2     3         1      3           2   
2            3         1       3    1    1     1         0      2           1   
3            4         1       1    1    2     3         0      3           2   
4            5         0       3    0    2     1         0      1           1   

   IsAlone  
0        0  
1        0  
2        1  
3        0  
4        1

In [76]:
test_df.head()

PassengerId  Pclass  Sex  Age  Fare  Embarked  Title  FamilySize  IsAlone
0          892       3    0    2     0         2      1           1        1
1          893       3    1    2     0         0      3           2        0
2          894       2    0    3     1         2      1           1        1
3          895       3    0    1     1         0      1           1        1
4          896       3    1    1     1         0      3           3        0

In [77]:
# y_train 구성
Pid_df = test_df['PassengerId']
# x_train 을 위한  survived 값 드롭
X_test_df= test_df

# 각 데이터셋의 피처 개수가 동일한 것을 확인

In [78]:
X_train.info()
print("*"*40)
X_test.info()
print("*"*40)
y_train.info()
print("*"*40)
y_test.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 712 entries, 333 to 703
Data columns (total 9 columns):
 #   Column       Non-Null Count  Dtype
---  ------       --------------  -----
 0   PassengerId  712 non-null    int64
 1   Pclass       712 non-null    int64
 2   Sex          712 non-null    int64
 3   Age          712 non-null    int64
 4   Fare         712 non-null    int64
 5   Embarked     712 non-null    int64
 6   Title        712 non-null    int64
 7   FamilySize   712 non-null    int64
 8   IsAlone      712 non-null    int64
dtypes: int64(9)
memory usage: 55.6 KB
****************************************
<class 'pandas.core.frame.DataFrame'>
Int64Index: 179 entries, 431 to 484
Data columns (total 9 columns):
 #   Column       Non-Null Count  Dtype
---  ------       --------------  -----
 0   PassengerId  179 non-null    int64
 1   Pclass       179 non-null    int64
 2   Sex          179 non-null    int64
 3   Age          179 non-null    int64
 4   Fare         179 non-nu

# 마찬가지로 train set과 피처의 개수가 같은것을 확인

In [79]:
X_test_df.info()
print("*"*40)
Pid_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 418 entries, 0 to 417
Data columns (total 9 columns):
 #   Column       Non-Null Count  Dtype
---  ------       --------------  -----
 0   PassengerId  418 non-null    int64
 1   Pclass       418 non-null    int64
 2   Sex          418 non-null    int64
 3   Age          418 non-null    int64
 4   Fare         418 non-null    int64
 5   Embarked     418 non-null    int64
 6   Title        418 non-null    int64
 7   FamilySize   418 non-null    int64
 8   IsAlone      418 non-null    int64
dtypes: int64(9)
memory usage: 29.5 KB
****************************************
<class 'pandas.core.series.Series'>
RangeIndex: 418 entries, 0 to 417
Series name: PassengerId
Non-Null Count  Dtype
--------------  -----
418 non-null    int64
dtypes: int64(1)
memory usage: 3.4 KB


# Logistic Regression 
 로지스틱 선형분석은 범주화된 변수와 하나 혹은 그 이상의 독립적 변수들의 상관과녜를 분석, 사건이 일어날 확률을 예측한다

In [80]:
logreg = LogisticRegression()
logreg.fit(X_train, y_train)
Y_pred = logreg.predict(X_test)
acc_log = round(logreg.score(X_test, y_test) * 100, 2) # accuracy percentage
acc_log

/home/dummy/anaconda3/envs/python/lib/python3.9/site-packages/sklearn/linear_model/_logistic.py:458: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(


84.92

# 결정트리

In [81]:
# Decision Tree

decision_tree = DecisionTreeClassifier()
decision_tree.fit(X_train, y_train)
Y_pred = decision_tree.predict(X_test)
acc_decision_tree_test = round(decision_tree.score(X_test, y_test) * 100, 2)
acc_decision_tree_test

77.65

# 랜덤포레스트

In [82]:
# Random Forest

random_forest = RandomForestClassifier()
random_forest.fit(X_train, y_train)
Y_pred = random_forest.predict(X_test)
random_forest.score(X_train, y_train)
acc_random_forest = round(random_forest.score(X_test, y_test) * 100, 2)
acc_random_forest

83.24

# 퍼셉트론

In [83]:
# Perceptron

perceptron = Perceptron()
perceptron.fit(X_train, y_train)
Y_pred = perceptron.predict(X_test)
acc_perceptron = round(perceptron.score(X_test, y_test) * 100, 2)
acc_perceptron

35.2

# XGboost

In [84]:
import xgboost as xgb
from sklearn.model_selection import train_test_split
from sklearn.metrics import classification_report, accuracy_score

xgboost = xgb.XGBClassifier()
xgboost.fit(X_train, y_train)
Y_pred = xgboost.predict(X_test)
acc_xgboost = round(xgboost.score(X_test,y_test) * 100, 2)
acc_xgboost

83.24

# 모델 평가

In [85]:
models = pd.DataFrame({
    'Model': ['Logistic Regression', 
              'Random Forest', 'Decision Tree','Perceptron','XGBoost'],
    'Score': [acc_log, acc_random_forest, acc_decision_tree_test,acc_perceptron,acc_xgboost]})
models.sort_values(by='Score', ascending=False)

Model  Score
0  Logistic Regression  84.92
1        Random Forest  83.24
4              XGBoost  83.24
2        Decision Tree  77.65
3           Perceptron  35.20

In [86]:
# VotingClassifier
from sklearn.ensemble import VotingClassifier

voting_ensemble = VotingClassifier(estimators=[("Random Forest",random_forest),
                                               ("XGBoost",xgboost)],
                                  voting = 'soft')
voting_ensemble.fit(X_train, y_train)
y_pred = voting_ensemble.predict(X_test)
acc_voting_ensemble= round(voting_ensemble.score(X_test,y_test) * 100, 2)
acc_voting_ensemble

83.24

In [87]:
# 전처리된 데이터를 저장
train_df.info()
test_df.info()
train_df.to_csv('train_df.csv', index=False)
test_df.to_csv('test_df.csv', index=False)

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 891 entries, 0 to 890
Data columns (total 10 columns):
 #   Column       Non-Null Count  Dtype
---  ------       --------------  -----
 0   PassengerId  891 non-null    int64
 1   Survived     891 non-null    int64
 2   Pclass       891 non-null    int64
 3   Sex          891 non-null    int64
 4   Age          891 non-null    int64
 5   Fare         891 non-null    int64
 6   Embarked     891 non-null    int64
 7   Title        891 non-null    int64
 8   FamilySize   891 non-null    int64
 9   IsAlone      891 non-null    int64
dtypes: int64(10)
memory usage: 69.7 KB
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 418 entries, 0 to 417
Data columns (total 9 columns):
 #   Column       Non-Null Count  Dtype
---  ------       --------------  -----
 0   PassengerId  418 non-null    int64
 1   Pclass       418 non-null    int64
 2   Sex          418 non-null    int64
 3   Age          418 non-null    int64
 4   Fare         418 non-null 

In [88]:
import joblib

joblib.dump(random_forest, './dev_rf.pkl')
joblib.dump(xgboost, './dev_xgb.pkl')
joblib.dump(voting_ensemble, './dev_vt.pkl')

['./dev_vt.pkl']

# 가장 적합한 모델은 XGBoost로 판단 됨

### binning (구역화) 진행하지 않았을때 ( test accuracy )
- random forest : 83.8
- xgboost : 79.33
- voting ensemble: 82.68

### binning (구역화) 진행하지 않았을때 ( kaggle score )
- random forest : 0.77751
- Xgboost : 0.77272
- voting ensemble : 0.77511

In [73]:
Y_pred = random_forest.predict(X_test_df)
submission = pd.DataFrame({
        "PassengerId": Pid_df,
        "Survived": Y_pred
    })
submission.to_csv('submission_preprocessing_randomForest.csv', index=False)

Y_pred = xgboost.predict(X_test_df)
submission = pd.DataFrame({
        "PassengerId": Pid_df,
        "Survived": Y_pred
    })
submission.to_csv('submission_preprocessing_XGBoost.csv', index=False)

Y_pred = voting_ensemble.predict(X_test_df)
submission = pd.DataFrame({
        "PassengerId": Pid_df,
        "Survived": Y_pred
    })
submission.to_csv('submission_preprocessing_voting_ensemble.csv', index=False)

/home/dummy/.local/lib/python3.10/site-packages/xgboost/data.py:312: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(dtype):
/home/dummy/.local/lib/python3.10/site-packages/xgboost/data.py:314: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  elif is_categorical_dtype(dtype) and enable_categorical:
/home/dummy/.local/lib/python3.10/site-packages/xgboost/data.py:345: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  if is_categorical_dtype(dtype)
/home/dummy/.local/lib/python3.10/site-packages/xgboost/data.py:336: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  return is_int or is_bool or is_float or is_categorical_dtyp

In [74]:
Y_pred = logreg.predict(X_test_df)
submission = pd.DataFrame({
        "PassengerId": Pid_df,
        "Survived": Y_pred
    })
submission.to_csv('submission_preprocessing_LogisticRegression.csv', index=False)

Y_pred = random_forest.predict(X_test_df)
submission = pd.DataFrame({
        "PassengerId": Pid_df,
        "Survived": Y_pred
    })
submission.to_csv('submission_preprocessing_randomForest.csv', index=False)

Y_pred = xgboost.predict(X_test_df)
submission = pd.DataFrame({
        "PassengerId": Pid_df,
        "Survived": Y_pred
    })
submission.to_csv('submission_preprocessing_XGBoost.csv', index=False)

Y_pred = voting_ensemble.predict(X_test_df)
submission = pd.DataFrame({
        "PassengerId": Pid_df,
        "Survived": Y_pred
    })
submission.to_csv('submission_preprocessing_voting_ensemble.csv', index=False)

/home/dummy/.local/lib/python3.10/site-packages/xgboost/data.py:312: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(dtype):
/home/dummy/.local/lib/python3.10/site-packages/xgboost/data.py:314: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  elif is_categorical_dtype(dtype) and enable_categorical:
/home/dummy/.local/lib/python3.10/site-packages/xgboost/data.py:345: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  if is_categorical_dtype(dtype)
/home/dummy/.local/lib/python3.10/site-packages/xgboost/data.py:336: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  return is_int or is_bool or is_float or is_categorical_dtyp

In [75]:
Y_pred = decision_tree.predict(X_test_df)
submission = pd.DataFrame({
        "PassengerId": Pid_df,
        "Survived": Y_pred
    })
submission.to_csv('submission_preprocessing_DecisionTree.csv', index=False)


# 실제 Submit 결과 Voting Ensemble이 가장 높은 Score를 획득함

## Hyper Parameter Tuning

In [89]:
import warnings
warnings.filterwarnings('ignore')
warnings.simplefilter(action='ignore', category=FutureWarning) 
'''
I've already completed feature engineering, handled missing data, and conducted data preprocessing. 
In my opinion, hyperparameter tuning is the most effective method for improving performance. 
Find tools and Python code for hyperparameter tuning of Random Forest, XGBoost, and a voting ensemble of Random Forest and XGBoost.
'''
# GridSearchCV and RandomizedSearchCV from Scikit-learn for Random Forest:
from sklearn.model_selection import GridSearchCV, RandomizedSearchCV
from sklearn.ensemble import RandomForestClassifier

# Define the parameter grid
param_grid = {
    'n_estimators': [100, 200, 300],
    'max_depth': [None, 10, 20],
    'min_samples_split': [2, 5, 10],
    'min_samples_leaf': [1, 2, 4],
    'max_features': ['auto', 'sqrt']
}

# Initialize the Random Forest classifier
# rf_classifier = RandomForestClassifier(random_state=42)

# Perform Grid Search
grid_search_rf = GridSearchCV(estimator=random_forest, param_grid=param_grid, cv=5, n_jobs=-1, verbose=2)
grid_search_rf.fit(X_train, y_train)

# Get the best parameters
best_params_rf = grid_search_rf.best_params_
print("Random forest - best parameter:", f'{best_params_rf}')

Fitting 5 folds for each of 162 candidates, totalling 810 fits
Random forest - best parameter: {'max_depth': 10, 'max_features': 'sqrt', 'min_samples_leaf': 1, 'min_samples_split': 5, 'n_estimators': 200}


In [90]:
best_rf_model = grid_search_rf.best_estimator_
best_rf_model

RandomForestClassifier(max_depth=10, min_samples_split=5, n_estimators=200)

In [95]:
# Initialize XGBoost classifier
# xgb_classifier = xgb.XGBClassifier(objective='binary:logistic', seed=42)
# XGBoost Hyperparameter Tuning:
import xgboost as xgb
from sklearn.model_selection import RandomizedSearchCV

# Define the parameter grid
param_grid = {
    'learning_rate': [0.01, 0.05, 0.1],
    'n_estimators': [100, 200, 300],
    'max_depth': [3, 5, 7],
    'min_child_weight': [1, 3, 5],
    'subsample': [0.5, 0.7, 0.9],
    'colsample_bytree': [0.5, 0.7, 0.9],
}

# Perform Randomized Search
random_search_xg = GridSearchCV(estimator=xgboost, param_grid = param_grid, cv=5, n_jobs=-1, verbose=2)
random_search_xg.fit(X_train, y_train)

# Get the best parameters
best_params_xgb = random_search_xg.best_params_
print("Xgboost - best parameter:", f'{best_params_xgb}')

Fitting 5 folds for each of 729 candidates, totalling 3645 fits


/home/dummy/.local/lib/python3.10/site-packages/xgboost/data.py:312: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(dtype):
/home/dummy/.local/lib/python3.10/site-packages/xgboost/data.py:314: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  elif is_categorical_dtype(dtype) and enable_categorical:
/home/dummy/.local/lib/python3.10/site-packages/xgboost/data.py:345: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  if is_categorical_dtype(dtype)
/home/dummy/.local/lib/python3.10/site-packages/xgboost/data.py:312: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(dtype):
/home/dummy/.local/lib/python3.10/site-package

/home/dummy/.local/lib/python3.10/site-packages/xgboost/data.py:312: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(dtype):
/home/dummy/.local/lib/python3.10/site-packages/xgboost/data.py:314: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  elif is_categorical_dtype(dtype) and enable_categorical:
/home/dummy/.local/lib/python3.10/site-packages/xgboost/data.py:345: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  if is_categorical_dtype(dtype)
/home/dummy/.local/lib/python3.10/site-packages/xgboost/data.py:336: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  return is_int or is_bool or is_float or is_categorical_dtyp

/home/dummy/.local/lib/python3.10/site-packages/xgboost/data.py:336: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  return is_int or is_bool or is_float or is_categorical_dtype(dtype)
/home/dummy/.local/lib/python3.10/site-packages/xgboost/data.py:312: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(dtype):
/home/dummy/.local/lib/python3.10/site-packages/xgboost/data.py:314: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  elif is_categorical_dtype(dtype) and enable_categorical:
/home/dummy/.local/lib/python3.10/site-packages/xgboost/data.py:345: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  if is_categorical_dtyp

/home/dummy/.local/lib/python3.10/site-packages/xgboost/data.py:312: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(dtype):
/home/dummy/.local/lib/python3.10/site-packages/xgboost/data.py:314: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  elif is_categorical_dtype(dtype) and enable_categorical:
/home/dummy/.local/lib/python3.10/site-packages/xgboost/data.py:345: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  if is_categorical_dtype(dtype)
/home/dummy/.local/lib/python3.10/site-packages/xgboost/data.py:336: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  return is_int or is_bool or is_float or is_categorical_dtyp

...

/home/dummy/.local/lib/python3.10/site-packages/xgboost/data.py:312: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(dtype):
/home/dummy/.local/lib/python3.10/site-packages/xgboost/data.py:314: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  elif is_categorical_dtype(dtype) and enable_categorical:
/home/dummy/.local/lib/python3.10/site-packages/xgboost/data.py:345: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  if is_categorical_dtype(dtype)
/home/dummy/.local/lib/python3.10/site-packages/xgboost/data.py:336: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  return is_int or is_bool or is_float or is_categorical_dtyp

/home/dummy/.local/lib/python3.10/site-packages/xgboost/data.py:312: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(dtype):
/home/dummy/.local/lib/python3.10/site-packages/xgboost/data.py:314: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  elif is_categorical_dtype(dtype) and enable_categorical:
/home/dummy/.local/lib/python3.10/site-packages/xgboost/data.py:345: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  if is_categorical_dtype(dtype)
/home/dummy/.local/lib/python3.10/site-packages/xgboost/data.py:336: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  return is_int or is_bool or is_float or is_categorical_dtyp

/home/dummy/.local/lib/python3.10/site-packages/xgboost/data.py:312: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(dtype):
/home/dummy/.local/lib/python3.10/site-packages/xgboost/data.py:314: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  elif is_categorical_dtype(dtype) and enable_categorical:
/home/dummy/.local/lib/python3.10/site-packages/xgboost/data.py:345: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  if is_categorical_dtype(dtype)
/home/dummy/.local/lib/python3.10/site-packages/xgboost/data.py:336: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  return is_int or is_bool or is_float or is_categorical_dtyp

/home/dummy/.local/lib/python3.10/site-packages/xgboost/data.py:312: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(dtype):
/home/dummy/.local/lib/python3.10/site-packages/xgboost/data.py:314: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  elif is_categorical_dtype(dtype) and enable_categorical:
/home/dummy/.local/lib/python3.10/site-packages/xgboost/data.py:345: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  if is_categorical_dtype(dtype)
/home/dummy/.local/lib/python3.10/site-packages/xgboost/data.py:336: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  return is_int or is_bool or is_float or is_categorical_dtyp

Xgboost - best parameter: {'colsample_bytree': 0.5, 'learning_rate': 0.05, 'max_depth': 5, 'min_child_weight': 1, 'n_estimators': 100, 'subsample': 0.9}


In [97]:
best_xgb_model = random_search_xg.best_estimator_
best_xgb_model

XGBClassifier(base_score=None, booster=None, callbacks=None,
              colsample_bylevel=None, colsample_bynode=None,
              colsample_bytree=0.5, early_stopping_rounds=None,
              enable_categorical=False, eval_metric=None, feature_types=None,
              gamma=None, gpu_id=None, grow_policy=None, importance_type=None,
              interaction_constraints=None, learning_rate=0.05, max_bin=None,
              max_cat_threshold=None, max_cat_to_onehot=None,
              max_delta_step=None, max_depth=5, max_leaves=None,
              min_child_weight=1, missing=nan, monotone_constraints=None,
              n_estimators=100, n_jobs=None, num_parallel_tree=None,
              predictor=None, random_state=None, ...)

In [96]:
# Ensemble Hyperparameter Tuning:

from sklearn.ensemble import VotingClassifier

# Initialize individual classifiers
# rf_classifier = RandomForestClassifier(random_state=42, **best_params_rf)  # using best parameters from RF tuning
# xgb_classifier = xgb.XGBClassifier(objective='binary:logistic', seed=42, **best_params_xgb)  # using best parameters from XGB tuning

# Create the voting ensemble
voting_classifier = VotingClassifier(estimators=[('rf', best_rf_model), ('xgb', best_xgb_model)])

# Define the parameter grid for voting classifier
param_grid_voting = {
    'voting': ['hard', 'soft'],
    'weights': [[1, 1], [2, 1], [1, 2]]  # weights for different classifiers in the ensemble
}

# Perform Grid Search
grid_search_voting = GridSearchCV(estimator=voting_classifier, param_grid=param_grid_voting, cv=5, n_jobs=-1, verbose=2)
grid_search_voting.fit(X_train, y_train)

# Get the best parameters
best_params_voting = grid_search_voting.best_params_
print("Voting Ensemble - best parameter:", f'{best_params_voting}')

Fitting 5 folds for each of 6 candidates, totalling 30 fits


/home/dummy/.local/lib/python3.10/site-packages/xgboost/data.py:312: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(dtype):
/home/dummy/.local/lib/python3.10/site-packages/xgboost/data.py:314: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  elif is_categorical_dtype(dtype) and enable_categorical:
/home/dummy/.local/lib/python3.10/site-packages/xgboost/data.py:345: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  if is_categorical_dtype(dtype)
/home/dummy/.local/lib/python3.10/site-packages/xgboost/data.py:336: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  return is_int or is_bool or is_float or is_categorical_dtyp

/home/dummy/.local/lib/python3.10/site-packages/xgboost/data.py:312: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(dtype):
/home/dummy/.local/lib/python3.10/site-packages/xgboost/data.py:314: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  elif is_categorical_dtype(dtype) and enable_categorical:
/home/dummy/.local/lib/python3.10/site-packages/xgboost/data.py:345: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  if is_categorical_dtype(dtype)
/home/dummy/.local/lib/python3.10/site-packages/xgboost/data.py:336: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  return is_int or is_bool or is_float or is_categorical_dtyp

/home/dummy/.local/lib/python3.10/site-packages/xgboost/data.py:312: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(dtype):
/home/dummy/.local/lib/python3.10/site-packages/xgboost/data.py:314: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  elif is_categorical_dtype(dtype) and enable_categorical:
/home/dummy/.local/lib/python3.10/site-packages/xgboost/data.py:345: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  if is_categorical_dtype(dtype)
/home/dummy/.local/lib/python3.10/site-packages/xgboost/data.py:336: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  return is_int or is_bool or is_float or is_categorical_dtyp

/home/dummy/.local/lib/python3.10/site-packages/xgboost/data.py:312: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(dtype):
/home/dummy/.local/lib/python3.10/site-packages/xgboost/data.py:314: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  elif is_categorical_dtype(dtype) and enable_categorical:
/home/dummy/.local/lib/python3.10/site-packages/xgboost/data.py:345: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  if is_categorical_dtype(dtype)
/home/dummy/.local/lib/python3.10/site-packages/xgboost/data.py:336: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  return is_int or is_bool or is_float or is_categorical_dtyp

/home/dummy/.local/lib/python3.10/site-packages/xgboost/data.py:312: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(dtype):
/home/dummy/.local/lib/python3.10/site-packages/xgboost/data.py:312: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(dtype):
/home/dummy/.local/lib/python3.10/site-packages/xgboost/data.py:314: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  elif is_categorical_dtype(dtype) and enable_categorical:
/home/dummy/.local/lib/python3.10/site-packages/xgboost/data.py:314: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  elif is_categorical_dtype(dtype) and enable_categorical:
/home/dummy/.local/l

Voting Ensemble - best parameter: {'voting': 'hard', 'weights': [2, 1]}


In [98]:
best_vt_model = grid_search_voting.best_estimator_
best_vt_model

VotingClassifier(estimators=[('rf',
                              RandomForestClassifier(max_depth=10,
                                                     min_samples_split=5,
                                                     n_estimators=200)),
                             ('xgb',
                              XGBClassifier(base_score=None, booster=None,
                                            callbacks=None,
                                            colsample_bylevel=None,
                                            colsample_bynode=None,
                                            colsample_bytree=0.5,
                                            early_stopping_rounds=None,
                                            enable_categorical=False,
                                            eval_metric=None,
                                            feature_types=None, gamma=None,
                                            gpu_id=Non...olicy=None,
                                            importance_type=None,
                                            interaction_constraints=None,
                                            learning_rate=0.01, max_bin=None,
                                            max_cat_threshold=None,
                                            max_cat_to_onehot=None,
                                            max_delta_step=None, max_depth=7,
                                            max_leaves=None, min_child_weight=3,
                                            missing=nan,
                                            monotone_constraints=None,
                                            n_estimators=100, n_jobs=None,
                                            num_parallel_tree=None,
                                            predictor=None, random_state=None, ...))],
                 weights=[2, 1])

In [99]:
acc_rf_best= best_rf_model.score(X_test,y_test)
print(acc_rf_best)
# test accuracy : 0.8603
acc_xgb_best= best_xgb_model.score(X_test,y_test)
print(acc_xgb_best)
# test accuracy : 0.8659
acc_vt_best= best_vt_model.score(X_test,y_test)
print(acc_vt_best)
# test accuracy : 0.8715

0.88268156424581
0.8659217877094972
0.8770949720670391


In [100]:
Y_pred = best_rf_model.predict(X_test_df)
submission = pd.DataFrame({
        "PassengerId": Pid_df,
        "Survived": Y_pred
    })
submission.to_csv('submission_opt_randomForest.csv', index=False)
# kaggle score (gridsearchcv) : 0.7679
# kaggle score (gridsearchcv): 0.7679

Y_pred = best_xgb_model.predict(X_test_df)
submission = pd.DataFrame({
        "PassengerId": Pid_df,
        "Survived": Y_pred
    })
submission.to_csv('submission_opt_XGBoost.csv', index=False)
# kaggle score (randomizedsearchcv): 0.7799
# kaggle score (gridsearchcv): 0.7679

Y_pred = best_vt_model.predict(X_test_df)
submission = pd.DataFrame({
        "PassengerId": Pid_df,
        "Survived": Y_pred
    })
submission.to_csv('submission_opt_voting_ensemble.csv', index=False)
# kaggle score (randomizedsearchcv): 0.7703
# kaggle score (gridsearchcv): 0.7679

[CV] END colsample_bytree=0.9, learning_rate=0.1, max_depth=3, min_child_weight=1, n_estimators=200, subsample=0.9; total time=   0.1s
[CV] END colsample_bytree=0.9, learning_rate=0.1, max_depth=3, min_child_weight=1, n_estimators=200, subsample=0.9; total time=   0.1s
[CV] END colsample_bytree=0.9, learning_rate=0.1, max_depth=3, min_child_weight=3, n_estimators=300, subsample=0.9; total time=   0.2s
[CV] END colsample_bytree=0.9, learning_rate=0.1, max_depth=3, min_child_weight=3, n_estimators=300, subsample=0.9; total time=   0.1s
[CV] END colsample_bytree=0.9, learning_rate=0.1, max_depth=3, min_child_weight=5, n_estimators=100, subsample=0.5; total time=   0.0s
[CV] END colsample_bytree=0.9, learning_rate=0.1, max_depth=3, min_child_weight=5, n_estimators=100, subsample=0.5; total time=   0.0s
[CV] END colsample_bytree=0.9, learning_rate=0.1, max_depth=5, min_child_weight=1, n_estimators=200, subsample=0.7; total time=   0.2s
[CV] END colsample_bytree=0.9, learning_rate=0.1, max_d

[CV] END colsample_bytree=0.9, learning_rate=0.05, max_depth=7, min_child_weight=5, n_estimators=300, subsample=0.5; total time=   0.2s
[CV] END colsample_bytree=0.9, learning_rate=0.05, max_depth=7, min_child_weight=5, n_estimators=300, subsample=0.7; total time=   0.2s
[CV] END colsample_bytree=0.9, learning_rate=0.05, max_depth=7, min_child_weight=5, n_estimators=300, subsample=0.7; total time=   0.2s
[CV] END colsample_bytree=0.9, learning_rate=0.1, max_depth=3, min_child_weight=3, n_estimators=200, subsample=0.9; total time=   0.1s
[CV] END colsample_bytree=0.9, learning_rate=0.1, max_depth=3, min_child_weight=3, n_estimators=200, subsample=0.9; total time=   0.1s
[CV] END colsample_bytree=0.9, learning_rate=0.1, max_depth=3, min_child_weight=3, n_estimators=200, subsample=0.9; total time=   0.1s
[CV] END colsample_bytree=0.9, learning_rate=0.1, max_depth=3, min_child_weight=3, n_estimators=300, subsample=0.5; total time=   0.1s
[CV] END colsample_bytree=0.9, learning_rate=0.1, ma

[CV] END colsample_bytree=0.9, learning_rate=0.05, max_depth=5, min_child_weight=5, n_estimators=200, subsample=0.7; total time=   0.1s
[CV] END colsample_bytree=0.9, learning_rate=0.05, max_depth=5, min_child_weight=5, n_estimators=200, subsample=0.7; total time=   0.1s
[CV] END colsample_bytree=0.9, learning_rate=0.05, max_depth=5, min_child_weight=5, n_estimators=200, subsample=0.7; total time=   0.1s
[CV] END colsample_bytree=0.9, learning_rate=0.05, max_depth=7, min_child_weight=1, n_estimators=200, subsample=0.7; total time=   0.2s
[CV] END colsample_bytree=0.9, learning_rate=0.05, max_depth=7, min_child_weight=1, n_estimators=200, subsample=0.7; total time=   0.1s
[CV] END colsample_bytree=0.9, learning_rate=0.05, max_depth=7, min_child_weight=1, n_estimators=200, subsample=0.9; total time=   0.2s
[CV] END colsample_bytree=0.9, learning_rate=0.05, max_depth=7, min_child_weight=1, n_estimators=200, subsample=0.9; total time=   0.2s
[CV] END colsample_bytree=0.9, learning_rate=0.0

[CV] END colsample_bytree=0.9, learning_rate=0.05, max_depth=5, min_child_weight=5, n_estimators=100, subsample=0.9; total time=   0.1s
[CV] END colsample_bytree=0.9, learning_rate=0.05, max_depth=7, min_child_weight=1, n_estimators=100, subsample=0.7; total time=   0.1s
[CV] END colsample_bytree=0.9, learning_rate=0.05, max_depth=7, min_child_weight=1, n_estimators=100, subsample=0.7; total time=   0.1s
[CV] END colsample_bytree=0.9, learning_rate=0.05, max_depth=7, min_child_weight=1, n_estimators=100, subsample=0.7; total time=   0.1s
[CV] END colsample_bytree=0.9, learning_rate=0.05, max_depth=7, min_child_weight=1, n_estimators=100, subsample=0.9; total time=   0.1s
[CV] END colsample_bytree=0.9, learning_rate=0.05, max_depth=7, min_child_weight=3, n_estimators=100, subsample=0.7; total time=   0.1s
[CV] END colsample_bytree=0.9, learning_rate=0.05, max_depth=7, min_child_weight=3, n_estimators=100, subsample=0.7; total time=   0.1s
[CV] END colsample_bytree=0.9, learning_rate=0.0

[CV] END colsample_bytree=0.9, learning_rate=0.05, max_depth=3, min_child_weight=5, n_estimators=200, subsample=0.7; total time=   0.1s
[CV] END colsample_bytree=0.9, learning_rate=0.05, max_depth=3, min_child_weight=5, n_estimators=200, subsample=0.7; total time=   0.1s
[CV] END colsample_bytree=0.9, learning_rate=0.05, max_depth=3, min_child_weight=5, n_estimators=200, subsample=0.7; total time=   0.1s
[CV] END colsample_bytree=0.9, learning_rate=0.05, max_depth=5, min_child_weight=1, n_estimators=300, subsample=0.7; total time=   0.2s
[CV] END colsample_bytree=0.9, learning_rate=0.05, max_depth=5, min_child_weight=1, n_estimators=300, subsample=0.7; total time=   0.2s
[CV] END colsample_bytree=0.9, learning_rate=0.05, max_depth=5, min_child_weight=1, n_estimators=300, subsample=0.9; total time=   0.2s
[CV] END colsample_bytree=0.9, learning_rate=0.05, max_depth=5, min_child_weight=1, n_estimators=300, subsample=0.9; total time=   0.2s
[CV] END colsample_bytree=0.9, learning_rate=0.0

[CV] END colsample_bytree=0.9, learning_rate=0.1, max_depth=3, min_child_weight=1, n_estimators=100, subsample=0.7; total time=   0.0s
[CV] END colsample_bytree=0.9, learning_rate=0.1, max_depth=3, min_child_weight=1, n_estimators=100, subsample=0.7; total time=   0.0s
[CV] END colsample_bytree=0.9, learning_rate=0.1, max_depth=3, min_child_weight=1, n_estimators=100, subsample=0.7; total time=   0.0s
[CV] END colsample_bytree=0.9, learning_rate=0.1, max_depth=3, min_child_weight=1, n_estimators=200, subsample=0.5; total time=   0.1s
[CV] END colsample_bytree=0.9, learning_rate=0.1, max_depth=3, min_child_weight=1, n_estimators=200, subsample=0.5; total time=   0.1s
[CV] END colsample_bytree=0.9, learning_rate=0.1, max_depth=3, min_child_weight=1, n_estimators=200, subsample=0.5; total time=   0.1s
[CV] END colsample_bytree=0.9, learning_rate=0.1, max_depth=3, min_child_weight=1, n_estimators=200, subsample=0.5; total time=   0.1s
[CV] END colsample_bytree=0.9, learning_rate=0.1, max_d